You can download the `requirements.txt` for this course from the workspace of this lab. `File --> Open...`

# L2: Create Agents to Research and Write an Article

In this lesson, you will be introduced to the foundational concepts of multi-agent systems and get an overview of the crewAI framework.

The libraries are already installed in the classroom. If you're running this notebook on your own machine, you can install the following:
```Python
!pip install crewai==0.28.8 crewai_tools==0.1.6 langchain_community==0.0.29
```

In [1]:
# Warning control
import warnings
warnings.filterwarnings('ignore')

- Import from the crewAI libray.

In [2]:
from crewai import Agent, Task, Crew
from crewai_tools import (
    #DirectoryReadTool,
    #FileReadTool,
    #SerperDevTool,
    #WebsiteSearchTool,
    #DOCXSearchTool,
    #RagTool,
    TXTSearchTool
)
from datetime import datetime

- As a LLM for your agents, you'll be using OpenAI's `gpt-3.5-turbo`.

**Optional Note:** crewAI also allow other popular models to be used as a LLM for your Agents. You can see some of the examples at the [bottom of the notebook](#1).

In [3]:
import os
from utils import get_openai_api_key

# Set up API keys

openai_api_key = get_openai_api_key()

os.environ["OPENAI_MODEL_NAME"] = 'gpt-3.5-turbo'
os.environ["OPENAI_API_KEY"] = "sk-proj-8nKBOgxInYCIqidcdSu7T3BlbkFJWac8qZbpFOE2TSn0OpId"


In [4]:
def call_crew_kickoff(str_current_datetime):
     # Instantiate tools
     #meeting_trans_docs_tool = DirectoryReadTool(directory='./meeting-transcription')
     #brd_temp_docs_tool = DirectoryReadTool(directory='./brd-template')
     #file_tool = FileReadTool()
     #web_rag_tool = WebsiteSearchTool()
     #docx_search_tool = DOCXSearchTool()
     #rag_tool = RagTool()
     mt_tool = TXTSearchTool(txt='./meeting-transcription/meeting-transcript_' + str_current_datetime + '.txt')
     brd_tool = TXTSearchTool(txt='./brd-template/brd-template.txt')

     text_parsing_agent = Agent(
        role="Text Interpreter",
        goal="Parse and interpret the raw text input, structuring it into manageable sections"
            "or data points that are relevant for analysis and processing.",
        backstory="You excel at deciphering complex textual data. You act as the first line of analysis,"
            "turning unstructured text into organized segments. You should enhance efficiency in data"
            "handling and support subsequent stages of data processing.",
        tools=[mt_tool],
        allow_delegation=True,
            verbose=True
     )

     data_extraction_agent = Agent(
          role="Data Extraction Agent",
          goal="Identify and extract essential data points, statistics,"
               "and specific information from the parsed text that are crucial"
               "for drafting a Business Requirements Document.",
          backstory="You should tackle the challenge of sifting through detailed textual data to"
               "find relevant information. You should be doing it with precision and speed, equipped"
               "with capabilities to recognize and categorize data efficiently, making it invaluable"
               "for projects requiring quick turnaround and accurate data handling.",
          tools=[mt_tool, brd_tool],
          allow_delegation=True,
          verbose=True
     )

     brd_compiler_agent = Agent(
          role="BRD Compiler",
          goal="Assemble the extracted data into a well-structured Business Requirements Document,"
               "ensuring that it is clear, coherent, and formatted according to standards.",
          backstory="You are a meticulous Business Requirement Document compiler, You should alleviate"
               "the burdens of manual document assembly. Ensure that all documents are crafted with"
               "precision, adhering to organizational standards, and ready for stakeholder review. You"
               "should be automating routine documentation tasks, thus allowing human team members to focus"
               "on more strategic activities.",
          tools=[brd_tool],
          allow_delegation=True,
          verbose=True
     )

     text_parsing = Task(
        description=(
            "1. Open and read the contents of the input text file.\n"
            "2. Analyze the document structure to identify headings, subheadings, and key paragraphs.\n"
            "3. Extract text under each identified section, ensuring context is preserved.\n"
            "4. Format the extracted text into a JSON structure with labels indicating the type"
                "of content (e.g., heading, detail)."
        ),
        expected_output="Structured JSON object containing separated sections of"
                        "text with labels based on their content type.",
        agent=text_parsing_agent,
     )

     data_extraction = Task(
        description=(
            "1. Take the JSON structured data from the Text Parsing Agent.\n"
            "2. Identify and extract specific data points like project goals, technical requirements,"
                "and stakeholder information.\n"
            "3. Organize the extracted data into relevant categories for easy access and use.\n"
            "4. Format all extracted data into a structured form suitable for document generation,"
                "ensuring it's ready for template insertion.\n"
        ),
        expected_output="A comprehensive list of key data points organized by category, ready for use in document generation.",
        agent=data_extraction_agent,
     )

     compile_brd = Task(
        description=(
            "1. Accept the structured and categorized data from the Data Extraction Agent.\n"
            "2. Open and read the BRD template for data insertion.\n"
            "3. Insert the received data into the respective sections of the BRD template.\n"
            "4. Apply formatting rules to ensure the document is professional and adheres to standards.\n"
            "5. Save the populated and formatted document as a new markdown file, marking the task as complete.\n"
        ),
        expected_output="A complete Business Requirements Document in markdown format, ready for review and distribution.",
        agent=brd_compiler_agent,
        output_file='generated-brd/brd_' + str_current_datetime + '.md',  # The final blog post will be saved here
     )

     crew = Crew(
        agents=[text_parsing_agent, data_extraction_agent, brd_compiler_agent],
        tasks=[text_parsing, data_extraction, compile_brd],
        verbose=2
     )

     result = crew.kickoff(inputs={'datetime': str_current_datetime})

     from IPython.display import Markdown
     Markdown(result)

## Creating Agents

- Define your Agents, and provide them a `role`, `goal` and `backstory`.
- It has been seen that LLMs perform better when they are role playing.

### Agent: Planner

**Note**: The benefit of using _multiple strings_ :
```Python
varname = "line 1 of text"
          "line 2 of text"
```

versus the _triple quote docstring_:
```Python
varname = """line 1 of text
             line 2 of text
          """
```
is that it can avoid adding those whitespaces and newline characters, making it better formatted to be passed to the LLM.

### Agent: Writer

### Agent: Editor

## Creating Tasks

- Define your Tasks, and provide them a `description`, `expected_output` and `agent`.

### Task: Plan

### Task: Write

In [5]:
'''    data_extraction = Task(
        description=(
            "1. Take the JSON structured data from the Text Parsing Agent.\n"
            "2. Identify and extract specific data points like project goals, technical requirements,"
                "and stakeholder information.\n"
            "3. Organize the extracted data into relevant categories for easy access and use.\n"
            "4. Format all extracted data into a structured form suitable for document generation,"
                "ensuring it's ready for template insertion.\n"
        ),
        expected_output="A comprehensive list of key data points organized by category, ready for use in document generation.",
        agent=data_extraction_agent,
    )
'''

'    data_extraction = Task(\n        description=(\n            "1. Take the JSON structured data from the Text Parsing Agent.\n"\n            "2. Identify and extract specific data points like project goals, technical requirements,"\n                "and stakeholder information.\n"\n            "3. Organize the extracted data into relevant categories for easy access and use.\n"\n            "4. Format all extracted data into a structured form suitable for document generation,"\n                "ensuring it\'s ready for template insertion.\n"\n        ),\n        expected_output="A comprehensive list of key data points organized by category, ready for use in document generation.",\n        agent=data_extraction_agent,\n    )\n'

### Task: Edit

In [6]:
'''    compile_brd = Task(
        description=(
            "1. Accept the structured and categorized data from the Data Extraction Agent.\n"
            "2. Open and read the BRD template for data insertion.\n"
            "3. Insert the received data into the respective sections of the BRD template.\n"
            "4. Apply formatting rules to ensure the document is professional and adheres to standards.\n"
            "5. Save the populated and formatted document as a new markdown file, marking the task as complete.\n"
        ),
        expected_output="A complete Business Requirements Document in markdown format, ready for review and distribution.",
        agent=brd_compiler_agent,
        output_file='generated-brd/brd_{datetime}.md',  # The final blog post will be saved here
    )
'''

'    compile_brd = Task(\n        description=(\n            "1. Accept the structured and categorized data from the Data Extraction Agent.\n"\n            "2. Open and read the BRD template for data insertion.\n"\n            "3. Insert the received data into the respective sections of the BRD template.\n"\n            "4. Apply formatting rules to ensure the document is professional and adheres to standards.\n"\n            "5. Save the populated and formatted document as a new markdown file, marking the task as complete.\n"\n        ),\n        expected_output="A complete Business Requirements Document in markdown format, ready for review and distribution.",\n        agent=brd_compiler_agent,\n        output_file=\'generated-brd/brd_{datetime}.md\',  # The final blog post will be saved here\n    )\n'

## Creating the Crew

- Create your crew of Agents
- Pass the tasks to be performed by those agents.
    - **Note**: *For this simple example*, the tasks will be performed sequentially (i.e they are dependent on each other), so the _order_ of the task in the list _matters_.
- `verbose=2` allows you to see all the logs of the execution. 

In [7]:
'''    crew = Crew(
        agents=[text_parsing_agent, data_extraction_agent, brd_compiler_agent],
        tasks=[text_parsing, data_extraction, compile_brd],
        verbose=2
    )
'''

'    crew = Crew(\n        agents=[text_parsing_agent, data_extraction_agent, brd_compiler_agent],\n        tasks=[text_parsing, data_extraction, compile_brd],\n        verbose=2\n    )\n'

## Running the Crew

**Note**: LLMs can provide different outputs for they same input, so what you get might be different than what you see in the video.

In [8]:
'''
    result = crew.kickoff(inputs={'datetime': str_current_datetime})

    from IPython.display import Markdown
    Markdown(result)
'''

"\n    result = crew.kickoff(inputs={'datetime': str_current_datetime})\n\n    from IPython.display import Markdown\n    Markdown(result)\n"

- Display the results of your execution as markdown in the notebook.

In [9]:
!python --version

Python 3.11.9


In [10]:
import gradio as gr

In [11]:
def process_file(input_file):
    current_datetime = datetime.now().strftime("%Y-%m-%d %H-%M-%S")
    print("Current date & time : ", current_datetime)
    
    # convert datetime obj to string
    str_current_datetime = str(current_datetime)

    fh = open(input_file, 'rb')
    #data = fh.read()

    # Ensure the target directory exists
    output_dir = "meeting-transcription"
    if not os.path.exists(output_dir):
        os.makedirs(output_dir)
    
    # Save the uploaded file to the specified folder with the specified name
    input_filepath = os.path.join(output_dir, "meeting-transcript_" + str_current_datetime + ".txt")
    with open(input_filepath, "wb") as file:
        file.write(fh.read())
    fh.close()

    call_crew_kickoff(str_current_datetime)

    # Example of processing: adding Markdown formatting. Replace this with your actual processing.
    #processed_text = "# Processed Output\n\n" + "\n".join(f"- {line}" for line in text.splitlines())
    
    output_filename = "generated-brd/brd_" + str_current_datetime + ".md"
    #with open(output_filename, "w") as file:
    #    file.write(processed_text)

    # Read the contents of the generated Markdown file
    with open(output_filename, "r") as md_file:
        markdown_content = md_file.read()

    # Return both the filename for download and the Markdown content for display
    return output_filename, markdown_content

In [12]:

with gr.Blocks() as demo:
    with gr.Row():
        file_input = gr.File(label="Upload a text file")
        download_btn = gr.File(label="Download Processed File in Markdown", file_count="single")
    with gr.Row():
        markdown_output = gr.Markdown()

    file_input.change(process_file, inputs=file_input, outputs=[download_btn, markdown_output])

demo.launch(share=True)


Running on local URL:  http://127.0.0.1:7860
Running on public URL: https://555181993525c76e6c.gradio.live

This share link expires in 72 hours. For free permanent hosting and GPU upgrades, run `gradio deploy` from Terminal to deploy to Spaces (https://huggingface.co/spaces)


Current date & time :  2024-06-09 17-53-45


Inserting batches in chromadb: 100%|██████████| 1/1 [00:00<00:00,  1.40it/s]


 [DEBUG]: == Working Agent: Text Interpreter
 [INFO]: == Starting Task: 1. Open and read the contents of the input text file.
2. Analyze the document structure to identify headings, subheadings, and key paragraphs.
3. Extract text under each identified section, ensuring context is preserved.
4. Format the extracted text into a JSON structure with labels indicating the typeof content (e.g., heading, detail).


> Entering new CrewAgentExecutor chain...
I need to start by searching the content of the input text file to understand its structure and identify headings, subheadings, and key paragraphs.

Action:
Search a txt's content

Action Input:
{
"search_query": "meeting-transcription/meeting-transcript_2024-06-09 17-53-45.txt"
}
 

Relevant Content:
Meeting Transcript: Extensive IT Project Requirements Discussion
 
Date: June 7, 2024
Time: 9:00 AM to 12:00 PM
Location: Conference Room B
Attendees:
 
Alex Johnson (Project Manager)
Sam Lee (Business Analyst)
Jessica Davis (Technical Lead) 